In [1]:
import pandas as pd
import numpy as np
import os
from sklearn.preprocessing import StandardScaler, MinMaxScaler
import random
from tqdm import tqdm
import matplotlib.pyplot as plt
import torch.nn as nn
from neuralforecast.losses.pytorch import BasePointLoss, _weighted_mean
import torch
from typing import Union
import warnings
# Filter specific warnings
warnings.filterwarnings("ignore", message="val_check_steps is greater than max_steps")
warnings.filterwarnings("ignore", message="The 'val_dataloader' does not have many workers")
warnings.filterwarnings("ignore", message="The 'train_dataloader' does not have many workers")
warnings.filterwarnings("ignore", message="The number of training batches")
warnings.filterwarnings("ignore", message="`Trainer.fit` stopped: `max_steps=16` reached.")
warnings.filterwarnings("ignore", message="Trying to infer the `batch_size` from an ambiguous collection")
import logging
logging.getLogger("pytorch_lightning").setLevel(logging.CRITICAL)
import pytorch_lightning as pl
# Trainer configuration
trainer = pl.Trainer(logger=False)

In [2]:
# Define the file name
file_path = 'BasicInputStaticProps.npy'

# Check if the file exists
if os.path.exists(file_path):
    # Load the .npy file with allow_pickle=True
    time_series_StaticProps = np.load(file_path, allow_pickle=True)
    print("Data loaded from file.")
else:
    print("File not found.")

    
StaticProps = pd.DataFrame(time_series_StaticProps, columns=["unique_id",
                        "p_mean","pet_mean","p_seasonality","frac_snow","aridity","high_prec_freq","high_prec_dur","low_prec_freq","low_prec_dur","carbonate_rocks_frac",
                        "geol_permeability","huc_02","soil_depth_pelletier","soil_depth_statsgo","soil_porosity","soil_conductivity","max_water_content",
                        "sand_frac","silt_frac","clay_frac","gauge_lat","gauge_lon","elev_mean","slope_mean","area_gages2","frac_forest","lai_max","lai_diff","gvf_max","gvf_diff"
                                                        ])
for col in StaticProps.columns:
    print(col)
    if col != 'ds' and col !='unique_id':
        # Global Normalization
        scaler = MinMaxScaler(feature_range=(0, 1))
        StaticProps[col] = scaler.fit_transform(StaticProps[[col]])
        
StaticProps['unique_id'] = StaticProps['unique_id'].astype(int)

Data loaded from file.
unique_id
p_mean
pet_mean
p_seasonality
frac_snow
aridity
high_prec_freq
high_prec_dur
low_prec_freq
low_prec_dur
carbonate_rocks_frac
geol_permeability
huc_02
soil_depth_pelletier
soil_depth_statsgo
soil_porosity
soil_conductivity
max_water_content
sand_frac
silt_frac
clay_frac
gauge_lat
gauge_lon
elev_mean
slope_mean
area_gages2
frac_forest
lai_max
lai_diff
gvf_max
gvf_diff


In [3]:
# Define the file name
file_path = 'BasicInputTimeSeries.npy'

# Check if the file exists
if os.path.exists(file_path):
    # Load the .npy file with allow_pickle=True
    time_series_data = np.load(file_path, allow_pickle=True)
    print("Data loaded from file.")
else:
    print("File not found.")


Data loaded from file.


In [4]:
#-------------------------------------------------------------
seed = 1
# Set the random seed for Python's random module
random.seed(seed)
# Set the random seed for NumPy
np.random.seed(seed)
print('seed :',seed)
#-------------------------------------------------------------

    
# Define the column names
columns = ["Year_Mnth_Day", "basin_id", "prcp(mm/day)", "srad(W/m2)", "tmax(C)", "tmin(C)", "vp(Pa)", "QObs(mm/d)"]
# Create the DataFrame
df = pd.DataFrame(time_series_data, columns=columns)

# Deleting the numpy array from memory
del time_series_data


# def cubic_root_positive(series: pd.Series) -> pd.Series:
#     # Convert series to numpy array for vectorized operations
#     arr = series.to_numpy()
    
#     # For values > 0, take cube root; for values <= 0, set to 0
#     arr_transformed = np.where(arr > 0, arr ** (1.0/3.0), 0.0)
    
#     # Convert the numpy array back to a pandas Series
#     return pd.Series(arr_transformed, index=series.index)


# df["prcp(mm/day)"] = cubic_root_positive(df["prcp(mm/day)"])
# df["QObs(mm/d)"] = cubic_root_positive(df["QObs(mm/d)"])

print(df)
for col in df.columns:
    print(col)
    if col != 'ds' and col !='unique_id' and col !='Year_Mnth_Day' and col !='basin_id':
        # Global Normalization
        scaler = MinMaxScaler(feature_range=(0, 1))
        df[col] = scaler.fit_transform(df[[col]])


df['ds'] = pd.to_datetime(df['Year_Mnth_Day'])
df['unique_id'] = df['basin_id']
df['unique_id'] = df['unique_id'].astype(int)
df['y'] = df['prcp(mm/day)'].astype(float)
df.drop(['Year_Mnth_Day', 'basin_id', "prcp(mm/day)", ], axis=1, inplace=True) # "srad(W/m2)", "tmax(C)", "tmin(C)", "vp(Pa)", "QObs(mm/d)"


        
# Sort the DataFrame by 'unique_id' and 'ds' to ensure correct order
df.sort_values(by=['unique_id', 'ds'], inplace=True)
# Set 'ds' as the index if you plan to use time-based indexing
df.set_index('ds', inplace=True, drop=False)
# Function to calculate EMA for each group
def calculate_ema(group, span):
    return group.ewm(span=span, adjust=False).mean()

# Apply the function to each group for multiple spans
span_settings = [2, 4, 6, 8, 10, 20, 50]  # Example spans
for span in span_settings:
    print(f'EMA_{span}')
    df[f'EMA_{span}'] = df.groupby('unique_id')['y'].transform(lambda x: calculate_ema(x, span))
    
df.reset_index(inplace=True, drop=True)
   

# Function to split each group
def splitter(data, n):
    train_frames = []
    test_frames = []
    for _, group in data.groupby('unique_id'):
        train, test = group[:-n], group[-n:]
        train_frames.append(train)
        test_frames.append(test)
    train_df = pd.concat(train_frames)
    test_df = pd.concat(test_frames)
    train_df.reset_index(inplace=True, drop=True)
    test_df.reset_index(inplace=True, drop=True)
    return train_df, test_df

# Function to drop the last n values fron each group
def drop_last_n(data, n):
    train_frames = []
    for _, group in data.groupby('unique_id'):
        train = group[:-n]
        train_frames.append(train)
    train_df = pd.concat(train_frames)
    train_df.reset_index(inplace=True, drop=True)
    return train_df
    
    
len_time_series = 7031
_, df = splitter(df, len_time_series)
    
    
    
    
    
# Identify unique time series
unique_ids = df['unique_id'].unique()
# Calculate the total number of time series
num_time_series = len(unique_ids)
# Ensure total number of time series is divisible by 10
if num_time_series % 10 != 0:
    excess_time_series = num_time_series % 10
    ids_to_drop = random.sample(list(unique_ids), excess_time_series)
    df = df[~df['unique_id'].isin(ids_to_drop)]
    unique_ids = df['unique_id'].unique()
    num_time_series = len(unique_ids)


    
# Split into 80% train and 20% test
num_train = (num_time_series * 8) // 10
num_test = num_time_series - num_train

# Ensure train and test splits are divisible by 10
if num_test % 10 != 0:
    adjustment = num_test % 10
    num_test -= adjustment
    num_train += adjustment

# Randomly shuffle and split
random.shuffle(unique_ids)
train_ids = unique_ids[:num_train]
test_ids = unique_ids[num_train:]

# Create train and test DataFrames
train_df = df[df['unique_id'].isin(train_ids)]
test_df = df[df['unique_id'].isin(test_ids)]

# Verify results
print(f"Number of time series: {num_time_series}")
print(f"Number of train time series: {len(train_ids)} (should be divisible by 10)")
print(f"Number of test time series: {len(test_ids)} (should be divisible by 10)")


print(train_df)
print('\n')
print(test_df)


StaticProps_train = StaticProps[StaticProps['unique_id'].isin(train_ids)]
StaticProps_test = StaticProps[StaticProps['unique_id'].isin(test_ids)]
    
    
print(StaticProps_test)
# # Number of records to be taken as test data for each unique_id
# n = 3000 
# n_time_series = 671
# len_time_series = 7000
# _, df = split_train_test(df, len_time_series)

# train_df, test_df = split_train_test(df, n)


# print("DataFrame:")
# print(df)



seed : 1
        Year_Mnth_Day  basin_id prcp(mm/day) srad(W/m2) tmax(C) tmin(C)  \
0          1989-10-02   1013500        10.38     247.88   15.32    2.72   
1          1989-10-02   1022500        12.31     276.67   17.28    3.26   
2          1989-10-02   1030500         3.21     281.52    18.8    1.13   
3          1989-10-02   1031500         2.57     276.44   17.95    3.16   
4          1989-10-02   1047000         5.77     291.58   18.02    0.27   
...               ...       ...          ...        ...     ...     ...   
4717796    2008-12-31  14309500        14.24     136.77    7.09   -0.43   
4717797    2008-12-31  14316700        11.05     125.75    1.75    -2.5   
4717798    2008-12-31  14325000        28.09     139.67    6.72    0.26   
4717799    2008-12-31  14362250         9.32     212.89    7.97   -3.74   
4717800    2008-12-31  14400000        12.77     174.73    8.15    0.13   

         vp(Pa) QObs(mm/d)  
0        748.12   0.321506  
1        853.67   0.553697  
2  

In [5]:
from neuralforecast.core import NeuralForecast
from neuralforecast.models import LSTM
from neuralforecast.losses.pytorch import MAE, MSE, QuantileLoss
from neuralforecast.auto import AutoNHITS, AutoPatchTST
from ray import tune
import torch.nn as nn


models = [LSTM(h = 1, context_size=256, input_size=-1 , max_steps=9*900, learning_rate=1e-3, loss= MSE(), random_seed=10, batch_size=64, scaler_type=None,
                    hist_exog_list =["EMA_2","EMA_4","EMA_6","EMA_8","EMA_10","EMA_20","EMA_50", "srad(W/m2)", "tmax(C)", "tmin(C)", "vp(Pa)", "QObs(mm/d)"],
                    stat_exog_list =["p_mean","pet_mean","p_seasonality","frac_snow","aridity","high_prec_freq","high_prec_dur","low_prec_freq","low_prec_dur","carbonate_rocks_frac",
                                    "geol_permeability","huc_02","soil_depth_pelletier","soil_depth_statsgo","soil_porosity","soil_conductivity","max_water_content",
                                    "sand_frac","silt_frac","clay_frac","gauge_lat","gauge_lon","elev_mean","slope_mean","area_gages2","frac_forest","lai_max","lai_diff","gvf_max","gvf_diff"]
              )]
nf = NeuralForecast(models=models, freq='1D', local_scaler_type=None)
nf.fit(train_df, static_df=StaticProps_train, verbose=True, val_size=0)




[rank: 0] Seed set to 10
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_steps=8100` reached.


In [6]:
# Precompute unique_ids and grouped data
unique_ids = test_df['unique_id'].unique()
grouped_data = {uid: test_df[test_df['unique_id'] == uid] for uid in unique_ids}

In [7]:
# torch.backends.cudnn.enabled = False


In [8]:
# Initialize variables
sequence_length = 256

# Create an empty DataFrame to store all predictions
all_preds = pd.DataFrame()
# Iterate through the DataFrame from the end, picking the desired slices
for index in range(len_time_series-2, sequence_length-1, -1):
    print("test :", index)
    subset_bag = []
    for unique_id in unique_ids:
        group_data = grouped_data[unique_id]
        group_data.reset_index(inplace=True, drop=True)
        subset = group_data.iloc[index - sequence_length:index + 1]
        subset_bag.append(subset)
        
    # Concatenate all subsets vertically into a single DataFrame
    data_part = pd.concat(subset_bag, ignore_index=True)    
    preds = nf.predict(data_part, static_df=StaticProps_test)
    preds = preds.reset_index(drop=False)
    all_preds = pd.concat([all_preds, preds], ignore_index=True)
    

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


test : 7029


Predicting: |          | 0/? [00:00<?, ?it/s]

test : 7028


/home/jrp5td/.local/lib/python3.10/site-packages/neuralforecast/core.py:196: FutureWarning: In a future version the predictions will have the id as a column. You can set the `NIXTLA_ID_AS_COL` environment variable to adopt the new behavior and to suppress this warning.
  warnings.warn(
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


...

/home/jrp5td/.local/lib/python3.10/site-packages/neuralforecast/core.py:196: FutureWarning: In a future version the predictions will have the id as a column. You can set the `NIXTLA_ID_AS_COL` environment variable to adopt the new behavior and to suppress this warning.
  warnings.warn(


test : 256


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

/home/jrp5td/.local/lib/python3.10/site-packages/neuralforecast/core.py:196: FutureWarning: In a future version the predictions will have the id as a column. You can set the `NIXTLA_ID_AS_COL` environment variable to adopt the new behavior and to suppress this warning.
  warnings.warn(


In [9]:

_, test_df_final = splitter(test_df, len_time_series-sequence_length-1)
all_preds.sort_values(by=['unique_id', 'ds'], inplace=True, ascending=[True, True])
all_preds.reset_index(inplace=True, drop=True)
results_df = test_df_final.copy()
results_df['LSTM'] = all_preds['LSTM'].values


In [10]:

def mean_absolute_error(y_true, y_pred):
    return np.mean(np.abs(y_true - y_pred))

def normalized_nash_sutcliffe_efficiencySTavg(y_true, y_pred):  # axis 0 space 1 time
    NSE = 1 - np.sum(np.square(y_true - y_pred)) / np.sum(np.square(y_true - np.mean(y_true)))
    return 1 / (2 - NSE)

def mean_squared_error(y_true, y_pred):
    return np.mean(np.square(y_true - y_pred))

def r_squared(y_true, y_pred):
    ss_res = np.sum(np.square(y_true - y_pred))
    ss_tot = np.sum(np.square(y_true - np.mean(y_true)))
    return 1 - (ss_res / ss_tot)

# Assuming your data is organized in results_df and reshaped
Y_ACTUAL = results_df['y'].values.reshape(num_test, len_time_series-sequence_length-1)
Y_HAT = results_df['LSTM'].values.reshape(num_test, len_time_series-sequence_length-1)

MAE = mean_absolute_error(Y_ACTUAL, Y_HAT)
MSE = mean_squared_error(Y_ACTUAL, Y_HAT)
NNSE = normalized_nash_sutcliffe_efficiencySTavg(Y_ACTUAL, Y_HAT)
R2 = r_squared(Y_ACTUAL, Y_HAT)

print("MSE: ", MSE)
print("MAE: ", MAE)
print("NNSE: ", NNSE)
print("R²: ", R2)


MSE:  0.00020385784674104617
MAE:  0.007074707674078919
NNSE:  0.7443110519170314
R²:  0.6564756798593524


In [11]:
MSE:  0.00020385784674104617
MAE:  0.007074707674078919
NNSE:  0.7443110519170314
R²:  0.6564756798593524

SyntaxError: invalid character '²' (U+00B2) (3905310564.py, line 4)

In [ ]:
results_df.to_pickle('LSTM_prcp_LB.pkl')